In [1]:
# from IPython.core.display import display, HTML
# display(HTML("<style>.container { width:100% !important; }</style>"))

In [1]:
import tensorflow as tf
import timeit
import os
os.environ["CUDA_VISIBLE_DEVICES"]="1"
from six.moves import cPickle
from text_utils import TextLoader
from tensorflow.contrib import rnn
from char_rnn_model import Model
import time
import math
import numpy as np
import text_utils as txt
from tensorflow.contrib import layers

# Define directories, hyperparameter

In [2]:
SEQLEN = 30
BATCHSIZE = 200
ALPHASIZE = 98
INTERNALSIZE = 512
NLAYERS = 3
learning_rate = 0.001  # fixed learning rate
dropout_pkeep = 0.8    # some dropout

# Load data using TextLoader object

In [3]:
shakedir = "shakespeare.txt"
#shakedir = "../tensorflow/**/*.py"
codetext, valitext, bookranges = txt.read_data_files(shakedir, validation=True)

# display some stats on the data
epoch_size = len(codetext) // (BATCHSIZE * SEQLEN)
txt.print_data_stats(len(codetext), len(valitext), epoch_size)

Loading file shakespeare.txt
Training text size is 4.36MB with 0.00KB set aside for validation. There will be 762 batches per epoch


# Create your model object

In [4]:
lr = tf.placeholder(tf.float32, name='lr') 
pkeep = tf.placeholder(tf.float32, name='pkeep') 
batchsize = tf.placeholder(tf.int32, name='batchsize')

# inputs
X = tf.placeholder(tf.uint8, [None, None], name='X')    # [ BATCHSIZE, SEQLEN ]
Xo = tf.one_hot(X, ALPHASIZE, 1.0, 0.0)                 # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# expected outputs = same sequence shifted by 1 since we are trying to predict the next character
Y_ = tf.placeholder(tf.uint8, [None, None], name='Y_')  # [ BATCHSIZE, SEQLEN ]
Yo_ = tf.one_hot(Y_, ALPHASIZE, 1.0, 0.0)               # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# input state
Hin = tf.placeholder(tf.float32, [None, INTERNALSIZE*NLAYERS], name='Hin')  # [ BATCHSIZE, INTERNALSIZE * NLAYERS]

cells = [rnn.GRUCell(INTERNALSIZE) for _ in range(NLAYERS)]

dropcells = [rnn.DropoutWrapper(cell,input_keep_prob=pkeep) for cell in cells]
multicell = rnn.MultiRNNCell(dropcells, state_is_tuple=False)
multicell = rnn.DropoutWrapper(multicell, output_keep_prob=pkeep)

Yr, H = tf.nn.dynamic_rnn(multicell, Xo, dtype=tf.float32, initial_state=Hin)

H = tf.identity(H, name='H')


Yflat = tf.reshape(Yr, [-1, INTERNALSIZE])    # [ BATCHSIZE x SEQLEN, INTERNALSIZE ]
Ylogits = layers.linear(Yflat, ALPHASIZE)     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Yflat_ = tf.reshape(Yo_, [-1, ALPHASIZE])     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
loss = tf.nn.softmax_cross_entropy_with_logits_v2(logits=Ylogits, labels=Yflat_)  # [ BATCHSIZE x SEQLEN ]
loss = tf.reshape(loss, [batchsize, -1])      # [ BATCHSIZE, SEQLEN ]
Yo = tf.nn.softmax(Ylogits, name='Yo')        # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Y = tf.argmax(Yo, 1)                          # [ BATCHSIZE x SEQLEN ]
Y = tf.reshape(Y, [batchsize, -1], name="Y")  # [ BATCHSIZE x SEQLEN ]
train_step = tf.train.AdamOptimizer(lr).minimize(loss)

# stats for display
seqloss = tf.reduce_mean(loss, 1)
batchloss = tf.reduce_mean(seqloss)
accuracy = tf.reduce_mean(tf.cast(tf.equal(Y_, tf.cast(Y, tf.uint8)), tf.float32))
loss_summary = tf.summary.scalar("batch_loss", batchloss)
acc_summary = tf.summary.scalar("batch_accuracy", accuracy)
summaries = tf.summary.merge([loss_summary, acc_summary])

timestamp = str(math.trunc(time.time()))
summary_writer = tf.summary.FileWriter("log/" + timestamp + "-training")
validation_writer = tf.summary.FileWriter("log/" + timestamp + "-validation")

if not os.path.exists("checkpoints"):
    os.mkdir("checkpoints")
saver = tf.train.Saver(max_to_keep=1000)

DISPLAY_FREQ = 50
_50_BATCHES = DISPLAY_FREQ * BATCHSIZE * SEQLEN
progress = txt.Progress(DISPLAY_FREQ, size=111+2, msg="Training on next "+str(DISPLAY_FREQ)+" batches")

from tensorflow_graph_in_jupyter import show_graph
show_graph(tf.get_default_graph())

# Training

In [5]:
gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=0.333)  
sess = tf.Session(config=tf.ConfigProto(gpu_options=gpu_options))
# init
istate = np.zeros([BATCHSIZE, INTERNALSIZE*NLAYERS])  # initial zero input state
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
step = 0

# training loop
for x, y_, epoch in txt.rnn_minibatch_sequencer(codetext, BATCHSIZE, SEQLEN, nb_epochs=10):

    # train on one minibatch
    feed_dict = {X: x, Y_: y_, Hin: istate, lr: learning_rate, pkeep: dropout_pkeep, batchsize: BATCHSIZE}
    _, y, ostate = sess.run([train_step, Y, H], feed_dict=feed_dict)

    # log training data for Tensorboard display a mini-batch of sequences (every 50 batches)
    if step % _50_BATCHES == 0:
        feed_dict = {X: x, Y_: y_, Hin: istate, pkeep: 1.0, batchsize: BATCHSIZE}  # no dropout for validation
        y, l, bl, acc, smm = sess.run([Y, seqloss, batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_learning_learned_comparison(x, y, l, bookranges, bl, acc, epoch_size, step, epoch)
        summary_writer.add_summary(smm, step)

    # run a validation step every 50 batches
    # The validation text should be a single sequence but that's too slow (1s per 1024 chars!),
    # so we cut it up and batch the pieces (slightly inaccurate)
    # tested: validating with 5K sequences instead of 1K is only slightly more accurate, but a lot slower.
    if step % _50_BATCHES == 0 and len(valitext) > 0:
        VALI_SEQLEN = 1*1024  # Sequence length for validation. State will be wrong at the start of each sequence.
        bsize = len(valitext) // VALI_SEQLEN
        txt.print_validation_header(len(codetext), bookranges)
        vali_x, vali_y, _ = next(txt.rnn_minibatch_sequencer(valitext, bsize, VALI_SEQLEN, 1))  # all data in 1 batch
        vali_nullstate = np.zeros([bsize, INTERNALSIZE*NLAYERS])
        feed_dict = {X: vali_x, Y_: vali_y, Hin: vali_nullstate, pkeep: 1.0,  # no dropout for validation
                     batchsize: bsize}
        ls, acc, smm = sess.run([batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_validation_stats(ls, acc)
        # save validation data for Tensorboard
        validation_writer.add_summary(smm, step)

    # display a short text generated with the current weights and biases (every 150 batches)
    if step // 3 % _50_BATCHES == 0:
        txt.print_text_generation_header()
        ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
        rh = np.zeros([1, INTERNALSIZE * NLAYERS])
        for k in range(1000):
            ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
            rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
            print(chr(txt.convert_to_alphabet(rc)), end="")
            ry = np.array([[rc]])
        txt.print_text_generation_footer()

    # save a checkpoint (every 500 batches)
    if step // 10 % _50_BATCHES == 0:
        saved_file = saver.save(sess, 'checkpoints/rnn_train_' + timestamp, global_step=step)
        print("Saved file: " + saved_file)

    # display progress bar
    progress.step(reset=step % _50_BATCHES == 0)

    # loop state around
    istate = ostate
    step += BATCHSIZE * SEQLEN


   0 (epoch 0) shakespeare.txt │ First Citizen:\Before we proce │                                │ loss: 4.47701
  30 (epoch 0) shakespeare.txt │ :\O,'tis Marcius!\Let's fetch  │                                │ loss: 4.51885
  60 (epoch 0) shakespeare.txt │ f the nobles.\\SICINIUS:\I wis │                                │ loss: 4.54516
  90 (epoch 0) shakespeare.txt │ u not set them on?\\MENENIUS:\ │                                │ loss: 4.53785
 120 (epoch 0) shakespeare.txt │ temples with the shows of peac │                                │ loss: 4.44243
 150 (epoch 0) shakespeare.txt │ an imagine.\\Third Servingman: │                                │ loss: 4.53774
 180 (epoch 0) shakespeare.txt │ trike the proud cedars 'gainst │                                │ loss: 4.47036
 210 (epoch 0) shakespeare.txt │ 'd imprisonment?\\HASTINGS:\Wi │                                │ loss: 4.55851
 240 (epoch 0) shakespeare.txt │ my lovely Edward's death,\Thei │                              

etgkaehd  o adt,uTdtru sreeYsrdTtuk odrorokoierkuccrtu oeuuuedd r TodoTe rU dtoU oeddTodiiirid T teTdddiduthodeiYhse eTeoueoo rrkukrkTo    ru reerUrdeuet  uuauuu otdaeiuhTukke ooeka dthtkaektkdood ttda  retkorTd ktdoorrakTitereoddt  uhtoo aaethuahtae dTehaa   rddrrrdurot(tuuerdeouu Ti utridTdio ee Uootdhhh teatTtooueeoret k ueoohuerodkeedku dTeodrdeeeuotkutederrtth(d rttuherTeheraTouedrraor(orooret((tdrroT o Tueui  TdtreiieU etYeoaeedddeeYa hYadddhhuduYuer eu soTdoudrsriroeie toodu uortidkh o Tttutu u hToeTaeukkurakhtethoee hu ktk uhthd ork Uhuohoh k UtUhtodhr dheedheu uerYt(dTu rkt o rdedi et tut  roTttre eraad a io k te ho du kueeutrheraktetktoatkhd kre  rrdTo tUoe kue ktkekd u eduokdrddYhdt rYYTetUeudt hotoraoe uu dokerTTttThdoattadhaeaa eaareToh  a a(euuu ueuter uteT htreashuroeru eeehde o  aordtd uirkTd ekdiu Utk  oe teduak uhaeekedu taoaouuddokdo  drrok  uuooudkUd  Ur   rTooi td ouoretUUeU  rdtto   aedroedr ero oeiiio eoiioot  oeoeu euohekhuedk ud ooookrd orukee tekduk eeehraedk


600000 (epoch 0) shakespeare.txt │ ever\Appear in your impediment │ ee  \aoo   tt t t  toet  t     │ loss: 3.10440
600030 (epoch 0) shakespeare.txt │ Condemning some to death, and  │ oo     t  tet  to t  t   to  t │ loss: 2.69114
600060 (epoch 0) shakespeare.txt │ of\ingrateful injury; to repor │ o  h   t   t ho  t   hhehe tt  │ loss: 3.32998
600090 (epoch 0) shakespeare.txt │ rance; if none, awake\Your dan │  t t  to te    toet   th  tet  │ loss: 3.11251
600120 (epoch 0) shakespeare.txt │  in the name o' the people\And │ ao tee te   to toe toettt  t   │ loss: 2.74745
600150 (epoch 0) shakespeare.txt │ ut insolent,\O'ercome with pri │ e te  t      h   t   tot  toet │ loss: 2.99475
600180 (epoch 0) shakespeare.txt │ at brought you forth this boy, │   hoe     h t tet   hee  toe   │ loss: 2.73040
600210 (epoch 0) shakespeare.txt │ bear the corse, and set it dow │ o t toe toe    ho  to  ho h t  │ loss: 2.54162
600240 (epoch 0) shakespeare.txt │ er; she is lunatic.\\QUEEN MAR │    hoe to to

900000 (epoch 0) shakespeare.txt │ r'd--\\First Citizen:\Well, si │ e   oAAEs   aoshse  \Thre  aos │ loss: 2.95271
900030 (epoch 0) shakespeare.txt │  can aid your action.\\MARCIUS │ torttnt tou  ane sn \\AARIIN:: │ loss: 2.19418
900060 (epoch 0) shakespeare.txt │ m not to be their bedfellow.\W │ eto  thute the s te   re   \\h │ loss: 2.35653
900090 (epoch 0) shakespeare.txt │ e unborn, could never be the m │  tn e    ao se to e  ae the te │ loss: 2.24452
900120 (epoch 0) shakespeare.txt │ out blows! Despising,\For you, │    aee e \Io  enes   Tou tou   │ loss: 2.50863
900150 (epoch 0) shakespeare.txt │ nger:\Yes, worthy sir,\The sla │      Io   aore e mose The toen │ loss: 2.29033
900180 (epoch 0) shakespeare.txt │ . There's no man in the world\ │ \Ihe   s to teretn the teree T │ loss: 2.05375
900210 (epoch 0) shakespeare.txt │ ead,\Or earth, gape open wide  │  n  To tot  e aote tue etos  t │ loss: 2.52868
900240 (epoch 0) shakespeare.txt │ the air.\\QUEEN MARGARET:\I'll │ he tns \\AOR

DNMURRUESURNYUNSS:
TO,,,
Al teesstherdan, I selees.

SETLT:
Ar we mre y itou gort an har.

COATU:UY wane alls burt ber oro anetosdisther.,
Mowt m morte anene, wod ird ancae is afitee, neat at ao har tee tret. Tir lou fonr. Fee ase inn me, the, wo me baren
O ose num ther ooleenote thoto,
Ine le movire tostart to memas ment, wiml dae fase mamlilo courite, sountall barg toan hath
I lesse have mereerand.T
AENDESE
::
Oot yaveli har teo frand, wat inginen ant intsase nan.

AANNS:
At seer sat srer ou taelid

As have norsattor mithire seers, wath oo thaseas

Tusar, all tis art yes serer sheants

om mote, sy ins the sicsastine

Same heres, tro worl, and the hemanereese,
Whan il lan tatsos ied inthes oodr

Teirs I morenathe, aratheac yertot ans marg ote thon athes at ilose
At essinese
aur tiths, she iinssacha houge,
To seed be bamse old, ham none be mans farereed of artheesssars
in sinlalde mit yer shard,-I houn some,
He ho meas for cesan io sheulthy botras and

I man has, ala, wheld myull as s


...

A man of him an honest side to the king,
And when the state of the sea of the service
Whose strength we seem a soldier for her head,
And that is so a prisoner. But that the dead
Hath
better seen the streets of her face and heard,
And with the way of the strange seat of the wars
That we have served his heart and have an earth
And strikes the states of the seat of him,
And with a strange and thing to bear the sea.

Second Servant:
Sir,
I will be the day to your soul with him to him.

LUCETTA:
Why,
The devil is a man,
That have the field of the chorce that we should be thousand.

DUKE SENIOR:
What say you, madam?

CASSIO:
If you do love, I think the death of the court.

Second Merchant:
I pray you, sir, to take your hands.

CARDINAL:
And therefore see you to your honour.

SILVIA:
I am no matter, I pray you,
I will ne'er say 'tis a good lift.

SICINIUS:
A provend to the court, and then, I take the countryman of a constant side of the s
└───────────────────────────────────────────────End of

44700000 (epoch 9) shakespeare.txt │ ere none.\\GLOUCESTER:\My lord │ re sote.\\CLOUCESTER:\Wy lord, │ loss: 0.53111
44700030 (epoch 9) shakespeare.txt │ s\The manner and the purpose o │ \The sar er ond mhe srrpose of │ loss: 0.90749
44700060 (epoch 9) shakespeare.txt │  it.\\BUCKINGHAM:\What says yo │ ht.\\KUCKINGHAM:\Whyt says tou │ loss: 0.60880
44700090 (epoch 9) shakespeare.txt │ h now, two tender playfellows  │  Iow  tho shnder mracsullows a │ loss: 1.41294
44700120 (epoch 9) shakespeare.txt │ .\\KING RICHARD III:\Slave, I  │ \\CING RICHARD III:\Woave, t w │ loss: 0.64090
44700150 (epoch 9) shakespeare.txt │ brace each other's love in ban │ race tnch mther s sive an trni │ loss: 1.07910
44700180 (epoch 9) shakespeare.txt │  so sweet a guest\As my sweet  │ temfoeet a srist\An ta boeet p │ loss: 1.51363
44700210 (epoch 9) shakespeare.txt │ is the Earl of Wiltshire? wher │ s nhe mnrl of Ganlsaire?\whare │ loss: 1.00549
44700240 (epoch 9) shakespeare.txt │ ll Norfolk be repeal'd: rep

45000000 (epoch 9) shakespeare.txt │ To those whose dealings have d │ h these those paat ng  wave ao │ loss: 1.23954
45000030 (epoch 9) shakespeare.txt │ ments,\Being nothing like the  │ ent\\\Au ng tot ing bike aoe s │ loss: 0.88772
45000060 (epoch 9) shakespeare.txt │ s land was guilty of.\Dighton  │  pond iis boilty of \\od t n t │ loss: 1.55281
45000090 (epoch 9) shakespeare.txt │ vil thus?\\KING RICHARD III:\A │ il,ooas?\\KING HICHARD III:\Tn │ loss: 0.66421
45000120 (epoch 9) shakespeare.txt │ , now, let Richmond and Elizab │  tot  tit mochaond tnd tnecane │ loss: 1.40931
45000150 (epoch 9) shakespeare.txt │  exile:\But little vantage sha │ avcle \Tut Iektle piltage ihal │ loss: 1.42919
45000180 (epoch 9) shakespeare.txt │  met, gentlemen:\I hope the ki │ aat \montlemen,\T wape the pin │ loss: 0.93492
45000210 (epoch 9) shakespeare.txt │ l our own but death\And that s │  tur hwn pes toath.Tnd thet wh │ loss: 1.29151
45000240 (epoch 9) shakespeare.txt │ uld\Learn him forbearance f

45005220 (epoch 9) shakespeare.txt │ e, man, and speak.\\IACHIMO:\U │   tyd  and toeak \\CAGHIMO:\In │ loss: 1.26447
45005250 (epoch 9) shakespeare.txt │  be gone;\While as the silly o │ te sone.\Ahice In the segee wf │ loss: 1.58078
45005280 (epoch 9) shakespeare.txt │ blind, an't please your grace. │ eond  mndt please your hrace \ │ loss: 0.87090
45005310 (epoch 9) shakespeare.txt │ r interest in those territorie │  hnjertst ts these thamsboryes │ loss: 1.27243
45005340 (epoch 9) shakespeare.txt │ ok into her blameful bed\Some  │ k tn o tir sroce ul soa.Th e s │ loss: 1.50358
45005370 (epoch 9) shakespeare.txt │  clouted shoon;\For they are t │ aoosdsd woowt,\Aor they are so │ loss: 1.47628
45005400 (epoch 9) shakespeare.txt │ QUEEN MARGARET:\For thousand Y │ UEEN MARGARET:\Tor theu and to │ loss: 0.78424
45005430 (epoch 9) shakespeare.txt │  my noble lord,\If she be so a │ sa loble lord, T  yhe be so mn │ loss: 1.00448
45005460 (epoch 9) shakespeare.txt │ ou do?'\\SIR TOBY BELCH:\'S

45600000 (epoch 9) shakespeare.txt │ ich is no grief to give.\\GLOU │ ch Is totmraef\to srve\\\HLOUC │ loss: 0.86199
45600030 (epoch 9) shakespeare.txt │ d up their caps,\And some ten  │  hp,the r cors,\And wh e thm t │ loss: 1.40577
45600060 (epoch 9) shakespeare.txt │ be not fix'd in doom perpetual │ eaaot son'd tn teur trrfocual  │ loss: 1.61556
45600090 (epoch 9) shakespeare.txt │ KING RICHARD III:\Where is thy │ ING HICHARD III:\Thare is the  │ loss: 0.39229
45600120 (epoch 9) shakespeare.txt │ t, the fair reverence of your  │   thenpotr sesenence of tour h │ loss: 0.93107
45600150 (epoch 9) shakespeare.txt │ ceives it is but faintly borne │ eive  tn in tet toirt y tern.. │ loss: 1.20272
45600180 (epoch 9) shakespeare.txt │ re.\Gentlemen, will you go mus │ e.\\ontlemen, thll you bo wast │ loss: 0.87824
45600210 (epoch 9) shakespeare.txt │  day.\\HENRY BOLINGBROKE:\So t │ oey.\\KELRY BOLINGBROKE:\Ai th │ loss: 0.67568
45600240 (epoch 9) shakespeare.txt │ ull of water:\That bucket d

# Generating Text

In [6]:
txt.print_text_generation_header()
ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
rh = np.zeros([1, INTERNALSIZE * NLAYERS])
for k in range(1000):
    ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
    rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
    print(chr(txt.convert_to_alphabet(rc)), end="")
    ry = np.array([[rc]])
txt.print_text_generation_footer()


┌───────────────────────────────────Generating random text from learned state───────────────────────────────────┐
:
The fair of men and the brow he hath been seen
A property of many to her head.

KING HENRY VI:
I am a son of this despate, I will
Thank thee to the provost: thou art no more
To me to bring, and so much more to me.

DON PEDRO:
It is no more to beat me to him and his sin
To have his service and her head. What shall be sent
To seek the first that he did see him how
I would not have him beaten. What is the man
That had been so much to be merried to his son?

HAMLET:
I will not see her here to his head.

PRINCE EDWARD:
I would not but to see the face of men
The sea of this shall have been better.

KING HENRY VI:
I will not be a strict of me.

KING RICHARD III:
We will not be a song of this son with him.

HAMLET:
How, then to the poor master to hear him?

DUKE VINCENTIO:
What is his majesty?

KATHARINA:
What is the matter?

PROSPERO:
I will not spit thee, sir.

KATHARINA:
What

In [ ]:
print()